In [12]:
!python --version

Python 3.9.16


## Discuss the dataset in general terms and describe why building a predictive model using this data might be practically useful.  Who could benefit from a model like this? Explain.

-- answer: Both the x-train and y-train dataset have 6920 observations in total, while the X-test dataset only has 1821. The dataset is about movie reviews, and the prediction will be extremely helpful to predict movie scores, and potentially helps theatres to allocate their seats and showing time better.

In [4]:
! pip install aimodelshare==0.0.189

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 967.8/967.8 kB 44.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 97.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.0/147.0 kB 17.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 28.4/28.4 MB 46.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 66.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 511.8/511.8 MB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.8/83.8 kB 11.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 322.5/322.5 kB 36.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.7/132.7 kB 17.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.0/294.0 kB 31.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.

In [ ]:
pip list

In [1]:
from aimodelshare import download_data
download_data('public.ecr.aws/y2e2a1d6/sst2_competition_data-repository:latest') 


Data downloaded successfully.


In [83]:
# Set up X_train, X_test, and y_train_labels objects
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=Warning)

X_train=pd.read_csv("sst2_competition_data/X_train.csv", squeeze=True)
X_test=pd.read_csv("sst2_competition_data/X_test.csv", squeeze=True)

y_train_labels=pd.read_csv("sst2_competition_data/y_train_labels.csv", squeeze=True)
y_train = pd.get_dummies(y_train_labels)

X_train.head()

0    The Rock is destined to be the 21st Century 's...
1    The gorgeously elaborate continuation of `` Th...
2    Singer/composer Bryan Adams contributes a slew...
3                 Yet the act is still charming here .
4    Whether or not you 're enlightened by any of D...
Name: text, dtype: object

## Run at least three prediction models to try to predict the SST sentiment dataset well.
Use an Embedding layer and LSTM layers in at least one model

Use an Embedding layer and Conv1d layers in at least one model

Use transfer learning with glove embeddings for at least one of these models

Discuss which models performed better and point out relevant hyper-parameter values for successful models.
Submit your best three models to the leader board for the SST Model Share competition.

### Embedding layer - model 1
model version: 442

Accuracy:77.39%	
f-1 score: 77.25%

For this model, i used embedding size of 16 and lenght of 10000. This is a simplied model without many hpyer parameters but it performs ok.

In [43]:
# Build a Document-Term Matrix (DTM) out of words in the training set 
# Remove stop words that occur too frequently to be useful, and 
# Use Term Frequency - Inverse Document Frequency (TF-IDF) formula to weight by how common words are generally

from sklearn.feature_extraction.text import TfidfVectorizer
tf_idf_vectorizer = TfidfVectorizer(stop_words='english')
tfidf_simple = tf_idf_vectorizer.fit(X_train)

In [44]:
# This preprocessor function makes use of the tf.keras tokenizer

from tensorflow import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.utils import pad_sequences
import numpy as np

# Build vocabulary from training text data
tokenizer = Tokenizer(num_words=10000)
tokenizer.fit_on_texts(X_train)

# preprocessor tokenizes words and makes sure all documents have the same length
def preprocessor(data, maxlen=40, max_words=10000):

    sequences = tokenizer.texts_to_sequences(data)

    word_index = tokenizer.word_index
    X = pad_sequences(sequences, maxlen=maxlen)

    return X

print(preprocessor(X_train).shape)
print(preprocessor(X_test).shape)

(6920, 40)
(1821, 40)


In [45]:
#Submit Model 1: 
from tensorflow.keras.layers import Dense, Embedding,Flatten
from tensorflow.keras.models import Sequential

model = Sequential()
model.add(Embedding(10000, 16, input_length=40))
model.add(Flatten())
model.add(Dense(2, activation='softmax'))
model.summary()

model.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['acc'])

history = model.fit(preprocessor(X_train), y_train,
                    epochs=10,
                    batch_size=32,
                    validation_split=0.2)


Model: "sequential_9"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_5 (Embedding)     (None, 40, 16)            160000    
                                                                 
 flatten_7 (Flatten)         (None, 640)               0         
                                                                 
 dense_7 (Dense)             (None, 2)                 1282      
                                                                 
Total params: 161,282
Trainable params: 161,282
Non-trainable params: 0
_________________________________________________________________
Epoch 1/10
173/173 [==============================] - 1s 4ms/step - loss: 0.6681 - acc: 0.6129 - val_loss: 0.8629 - val_acc: 0.1488
Epoch 2/10
173/173 [==============================] - 1s 3ms/step - loss: 0.6210 - acc: 0.6266 - val_loss: 0.8252 - val_acc: 0.2139
Epoch 3/10
173/173 [============================

In [46]:
import aimodelshare as ai
ai.export_preprocessor(preprocessor,"") 

Your preprocessor is now saved to 'preprocessor.zip'


In [11]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [12]:
#Set credentials using modelshare.org username/password

from aimodelshare.aws import set_credentials
    
apiurl="https://rlxjxnoql9.execute-api.us-east-1.amazonaws.com/prod/m" #This is the unique rest api that powers this specific Playground

set_credentials(apiurl=apiurl)

AI Modelshare Username:··········
AI Modelshare Password:··········
AI Model Share login credentials set successfully.


In [13]:
#Instantiate Competition

mycompetition= ai.Competition(apiurl)

In [14]:
#Submit Model 1: 

#-- Generate predicted y values (Model 1)
#Note: Keras predict returns the predicted column index location for classification models
prediction_column_index=model.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 1 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

57/57 [==============================] - 0s 1ms/step
Insert search tags to help users find your model (optional): model1
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 442

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [15]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

### Embedding layer and LSTM -model 2
model version: 449

Accuracy:51.92% 

f-1 score:37.72%

hyper parameters: an embedding size of 16 and vocab lenght of 10000, LSTM units of 16 and 32. The prediction isn't very well.

In [47]:
# Train and submit model 2 using same preprocessor (note that you could save a new preprocessor, but we will use the same one for this example).
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, LSTM, Flatten

model2 = Sequential()
model2.add(Embedding(10000, 16, input_length=40))
model2.add(LSTM(16, return_sequences=True, dropout=0.2))
model2.add(LSTM(32, dropout=0.2))
model2.add(Flatten())
model2.add(Dense(2, activation='softmax'))

model2.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model2.fit(preprocessor(X_train), y_train,
                    epochs=1,
                    batch_size=32,
                    validation_split=0.2)

173/173 [==============================] - 14s 60ms/step - loss: 0.6594 - acc: 0.6156 - val_loss: 0.9265 - val_acc: 0.1655


In [48]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model2, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model2.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [49]:
#Submit Model 2: 

#-- Generate predicted y values (Model 2)
prediction_column_index=model2.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 2 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model2.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

57/57 [==============================] - 2s 18ms/step
Insert search tags to help users find your model (optional): model2
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 449

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [50]:
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

model version:449
accuracy:51.92%
f-1 score: 37.72%	

In [ ]:
# Compare two or more models 
data=mycompetition.compare_models([1, 2], verbose=1)
mycompetition.stylize_compare(data)

### Embedding layer and Conv1d layers - model 3

model version: 452

Accuracy: 78.49%	

f-1 score:78.29

hyperpameters: an embedding size of 16 and vocab lenght of 10000, using one Cov1D layer of 32 units. Model 3 performs the best out of all three models.



In [ ]:
pip download tensorflow

In [17]:
#Import the required libraries
import numpy as np
import tensorflow as tf

################Note that we are using tf.keras, not keras!#####################################
import tensorflow.keras as keras

from keras.datasets import mnist

In [84]:
from tensorflow.keras.layers import Conv1D, Dense, Embedding, GlobalMaxPooling1D
from tensorflow.keras.models import Sequential

model3 = Sequential()
model3.add(Embedding(10000, 16, input_length=40))
model3.add(Conv1D(32, 5, activation='relu'))
model3.add(GlobalMaxPooling1D())
model3.add(Dense(2, activation='softmax'))
model3.summary()

model3.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['acc'])

history = model3.fit(preprocessor(X_train), y_train,
                    epochs=10,
                    batch_size=32,
                    validation_split=0.2)

Model: "sequential_16"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_8 (Embedding)     (None, 40, 16)            160000    
                                                                 
 conv1d_1 (Conv1D)           (None, 36, 32)            2592      
                                                                 
 global_max_pooling1d_1 (Glo  (None, 32)               0         
 balMaxPooling1D)                                                
                                                                 
 dense_15 (Dense)            (None, 2)                 66        
                                                                 
Total params: 162,658
Trainable params: 162,658
Non-trainable params: 0
_________________________________________________________________
Epoch 1/10
173/173 [==============================] - 2s 6ms/step - loss: 0.6638 - acc: 0.6091 - val_loss: 0.8407

In [86]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model3 = model_to_onnx(model3, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model3.onnx", "wb") as f:
    f.write(onnx_model3.SerializeToString())

In [87]:
#Set credentials using modelshare.org username/password

from aimodelshare.aws import set_credentials
    
apiurl="https://rlxjxnoql9.execute-api.us-east-1.amazonaws.com/prod/m" #This is the unique rest api that powers this specific Playground

set_credentials(apiurl=apiurl)

AI Modelshare Username:··········
AI Modelshare Password:··········
AI Model Share login credentials set successfully.


In [88]:
mycompetition= ai.Competition(apiurl)

In [89]:
#Submit Model 3: 

#-- Generate predicted y values (Model 1)
#Note: Keras predict returns the predicted column index location for classification models
prediction_column_index=model3.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 1 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model3.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

57/57 [==============================] - 0s 2ms/step
Insert search tags to help users find your model (optional): model3
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 452

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [90]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

In [18]:
from keras.models import Sequential
from keras.layers.core import Dense, Activation, Flatten

In [19]:
from keras.layers.convolutional import Conv2D
from keras.layers.pooling import MaxPooling2D

In [20]:
from keras.utils import np_utils
from tensorflow.keras.optimizers import SGD

### transfer learning - model 4

Accuracy: 51.92%	

f-1 score: 37.72%


In [93]:
# Here are several classic ML architectures you can choose from to experiment with next:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import BaggingClassifier
from sklearn.ensemble import GradientBoostingClassifier


#Example code to fit model:
model = GradientBoostingClassifier(n_estimators=50, learning_rate=1.0,
    max_depth=1, random_state=0).fit(preprocessor(X_train), y_train_labels)
model.score(preprocessor(X_train), y_train_labels)

# Save sklearn model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx


feature_count=preprocessor(X_test).shape[1] #Get count of preprocessed features
#initial_type = [('float_input', FloatTensorType([None, feature_count]))]  # Insert correct number of preprocessed features

onnx_model = model_to_onnx(model, framework='sklearn',
                          #initial_types=initial_type,
                          transfer_learning=True,
                          deep_learning=False)

with open("model.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

#-- Generate predicted values (a list of predicted labels "real" or "fake")
prediction_labels = model.predict(preprocessor(X_test))

# Submit model to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)


Insert search tags to help users find your model (optional): model4
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 453

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [95]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

### New LSTM model - model 5

Accuracy: 51.37%	

f-1 score:50.48%

Hyper parameters: embedding size of 16, vocab length of 10,000,and two LSTM units of 16 in both first and second layer. Inspired by model 2.

In [100]:
model5 = Sequential()
model5.add(Embedding(10000, 16, input_length=40))
model5.add(LSTM(16, return_sequences=True, dropout=0.2))
model5.add(LSTM(16, dropout=0.2))
model5.add(Flatten())
model5.add(Dense(2, activation='softmax'))

model5.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model5.fit(preprocessor(X_train), y_train,
                    epochs=10,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/10
173/173 [==============================] - 16s 76ms/step - loss: 0.6655 - acc: 0.6136 - val_loss: 0.8288 - val_acc: 0.1496
Epoch 2/10
173/173 [==============================] - 6s 35ms/step - loss: 0.5614 - acc: 0.7153 - val_loss: 0.7857 - val_acc: 0.5672
Epoch 3/10
173/173 [==============================] - 9s 49ms/step - loss: 0.4284 - acc: 0.8168 - val_loss: 0.7784 - val_acc: 0.6221
Epoch 4/10
173/173 [==============================] - 8s 47ms/step - loss: 0.3503 - acc: 0.8548 - val_loss: 0.6178 - val_acc: 0.7312
Epoch 5/10
173/173 [==============================] - 7s 41ms/step - loss: 0.2893 - acc: 0.8806 - val_loss: 0.5899 - val_acc: 0.7406
Epoch 6/10
173/173 [==============================] - 9s 54ms/step - loss: 0.2507 - acc: 0.8978 - val_loss: 0.7085 - val_acc: 0.7045
Epoch 7/10
173/173 [==============================] - 7s 38ms/step - loss: 0.2196 - acc: 0.9122 - val_loss: 0.5502 - val_acc: 0.7811
Epoch 8/10
173/173 [==============================] - 7s 40ms/step -

In [102]:
onnx_model5 = model_to_onnx(model5, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model5.onnx", "wb") as f:
    f.write(onnx_model5.SerializeToString())

In [103]:
#-- Generate predicted values (a list of predicted labels "real" or "fake")
prediction_labels = model5.predict(preprocessor(X_test))

# Submit model to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model5.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

57/57 [==============================] - 1s 11ms/step
Insert search tags to help users find your model (optional): model5
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 454

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


### New LSTM model - model 6

Accuracy: 80.39%

f-1 score: 81.65%

hyper parameters: i modified model 6 based on model 5 results, changing LSTM units from 16 to 32. 


In [105]:
model6 = Sequential()
model6.add(Embedding(10000, 16, input_length=40))
model6.add(LSTM(32, return_sequences=True, dropout=0.2))
model6.add(LSTM(32, dropout=0.2))
model6.add(Flatten())
model6.add(Dense(2, activation='softmax'))

model6.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model6.fit(preprocessor(X_train), y_train,
                    epochs=10,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/10
173/173 [==============================] - 23s 87ms/step - loss: 0.6541 - acc: 0.6154 - val_loss: 0.8022 - val_acc: 0.2413
Epoch 2/10
173/173 [==============================] - 12s 68ms/step - loss: 0.5107 - acc: 0.7551 - val_loss: 0.6991 - val_acc: 0.6373
Epoch 3/10
173/173 [==============================] - 13s 78ms/step - loss: 0.3821 - acc: 0.8320 - val_loss: 0.5645 - val_acc: 0.7587
Epoch 4/10
173/173 [==============================] - 8s 48ms/step - loss: 0.3127 - acc: 0.8690 - val_loss: 0.6872 - val_acc: 0.7247
Epoch 5/10
173/173 [==============================] - 8s 47ms/step - loss: 0.2673 - acc: 0.8923 - val_loss: 0.6301 - val_acc: 0.7457
Epoch 6/10
173/173 [==============================] - 8s 47ms/step - loss: 0.2257 - acc: 0.9090 - val_loss: 0.5481 - val_acc: 0.7738
Epoch 7/10
173/173 [==============================] - 6s 33ms/step - loss: 0.1973 - acc: 0.9184 - val_loss: 0.5544 - val_acc: 0.7623
Epoch 8/10
173/173 [==============================] - 8s 45ms/step

In [106]:
onnx_model6 = model_to_onnx(model6, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model6.onnx", "wb") as f:
    f.write(onnx_model5.SerializeToString())

In [107]:
#-- Generate predicted values (a list of predicted labels "real" or "fake")
prediction_labels = model6.predict(preprocessor(X_test))

# Submit model to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model6.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels)

57/57 [==============================] - 1s 11ms/step
Insert search tags to help users find your model (optional): model6
Provide any useful notes about your model (optional): 

Your model has been submitted as model version 455

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


### Discuss which models performed better and point out relevant hyper-parameter values for successful models. Submit your best three models to the leader board for the SST Model Share competition.

Overall, I adjusted the first 3 models based on group discussions, and proposed 6 models in total. Out of the 6 models, the best performing one is adjusted LSTM with embedding layers, which has LSTM units of 32 and has an embedding layer of 16, a vocabulatory length of 10,000.

The Conv1D model also perfroms quite good, with important hyper parameters of COv1D layer of (32,5) .